# NLP-LAB Exercise 01 by jonas weinz
----
## links:

* Article: https://miguelmalvarez.com/2017/03/23/how-can-machine-learning-and-ai-help-solving-the-fake-news-problem/
    * corresponding code: https://github.com/kjam/random_hackery/blob/master/Attempting%20to%20detect%20fake%20news.ipynb

* Tutorial on Datacamp: https://www.datacamp.com/community/tutorials/scikit-learn-fake-news

* liar dataset paper: https://www.cs.ucsb.edu/~william/papers/acl2017.pdf
    * dataset: https://www.cs.ucsb.edu/~william/data/liar_dataset.zip

## Dependencies for this Notebook:
* library [rdflib](https://github.com/RDFLib/rdflib)
    * install: `pip3 install rdflib`


In [1]:
%pylab ipympl

Populating the interactive namespace from numpy and matplotlib


In [21]:
import pandas as pd
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import PassiveAggressiveClassifier
from sklearn.naive_bayes import MultinomialNB
from sklearn import metrics
import matplotlib.pyplot as plt
from pprint import pprint as pp
import os

## Tools used later

In [37]:
def plot_confusion_matrix(cm, classes,
                          title,
                          normalize=False,
                          cmap=plt.cm.Blues):
    fig_1, ax_1 = plt.subplots()
    """
    See full source and example: 
    http://scikit-learn.org/stable/auto_examples/model_selection/plot_confusion_matrix.html
    
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title('Confusion Matrix for: ' + title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)

    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')

    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, cm[i, j],
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")

    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label')

## Generate/Download Datasets we are working on

* running bash script to download all needed data and store it into the `data` subfolder

In [3]:
%%bash
./Task_2_gen_data.sh

downloading and unpacking https://www.cs.ucsb.edu/~william/data/liar_dataset.zip if not already existing
UnZip 6.00 of 20 April 2009, by Debian. Original by Info-ZIP.

Latest sources and executables are at ftp://ftp.info-zip.org/pub/infozip/ ;
see ftp://ftp.info-zip.org/pub/infozip/UnZip.html for other sites.

Compiled with gcc 6.3.0 20170415 for Unix (Linux ELF).

UnZip special compilation options:
        ACORN_FTYPE_NFS
        COPYRIGHT_CLEAN (PKZIP 0.9x unreducing method not supported)
        SET_DIR_ATTRIB
        SYMLINKS (symbolic links supported, if RTL and file system permit)
        TIMESTAMP
        UNIXBACKUP
        USE_EF_UT_TIME
        USE_UNSHRINK (PKZIP/Zip 1.x unshrinking method supported)
        USE_DEFLATE64 (PKZIP 4.x Deflate64(tm) supported)
        UNICODE_SUPPORT [wide-chars, char coding: UTF-8] (handle UTF-8 paths)
        LARGE_FILE_SUPPORT (large files over 2 GiB supported)
        ZIP64_SUPPORT (archives using Zip64 for large files supported)
        USE

## Read in fake news table

In [4]:
df_1 = pd.read_csv('data/fake_or_real_news.csv').set_index('Unnamed: 0')

* display first 10 entries

In [5]:
display(df_1.shape)
display(df_1[:10])

(6335, 3)

title  \
Unnamed: 0                                                      
8476                             You Can Smell Hillary’s Fear   
10294       Watch The Exact Moment Paul Ryan Committed Pol...   
3608              Kerry to go to Paris in gesture of sympathy   
10142       Bernie supporters on Twitter erupt in anger ag...   
875          The Battle of New York: Why This Primary Matters   
6903                                              Tehran, USA   
7341        Girl Horrified At What She Watches Boyfriend D...   
95                          ‘Britain’s Schindler’ Dies at 106   
4869        Fact check: Trump and Clinton at the 'commande...   
2909        Iran reportedly makes new push for uranium con...   

                                                         text label  
Unnamed: 0                                                           
8476        Daniel Greenfield, a Shillman Journalism Fello...  FAKE  
10294       Google Pinterest Digg Linkedin Reddit Stumbleu...  FAKE  
3608        U.S. Secretary of State John F. Kerry said Mon...  REAL  
10142       — Kaydee King (@KaydeeKing) November 9, 2016 T...  FAKE  
875         It's primary day in New York and front-runners...  REAL  
6903          \nI’m not an immigrant, but my grandparents ...  FAKE  
7341        Share This Baylee Luciani (left), Screenshot o...  FAKE  
95          A Czech stockbroker who saved more than 650 Je...  REAL  
4869        Hillary Clinton and Donald Trump made some ina...  REAL  
2909        Iranian negotiators reportedly have made a las...  REAL

* create test dataset

In [6]:
def create_training_and_test_set(dset, cutoff=0.7):
    shuffled = sku.shuffle(dset) # shuffle dataset
    y = shuffled.label
    shuffled = shuffled.drop('label', axis=1)['text']
    size = int(cutoff * shuffled.shape[0])
    return shuffled[:size], y[:size], shuffled[size:], y[size:]
    

In [7]:
X,y, Xt,yt = create_training_and_test_set(df_1)

In [8]:
#X2,y2, Xt2,yt2 = train_test_split(df_1['text'],df_1.label,test_size=0.3)

In [9]:
X

Unnamed: 0
5507     Anthony Weiner Sends Apology Sext To Entire Cl...
1440     John Kasich was killing it with these Iowa vot...
3172     Yeah, yeah, with the rise of Der Trumper and t...
6962     Vermont fights the opioid epidemic by limiting...
6970     — Adam Baldwin (@AdamBaldwin) October 28, 2016...
7209     Militias prepare for election unrest while Chr...
4781     Raleigh, North Carolina (CNN) As soon as the f...
6137     Yemen’s Hudaydah suffering from dire humanitar...
8799     Subscribe \nIn politics, the Third Way is a po...
4374     Hanging in the balance is Obama’s vision of Am...
9465     Under the Surface - Naomi Klein and the Great ...
10409    October 28, 2016 at 9:00 PM \nWhy would Putin ...
2822     HAMPTON, N.H. -- Hillary Rodham Clinton said F...
5190     (CNN) Donald Trump on Wednesday refused to say...
2286     Gay rights won't fade as a political issue. Th...
4308     Fox Business’s Tuesday night Republican debate...
7305     Yes, There Are Paid Government Troll

In [10]:
count_vectorizer = CountVectorizer(stop_words='english')
count_train = count_vectorizer.fit_transform(X)
count_test = count_vectorizer.transform(Xt)

In [11]:
tfidf_vectorizer = TfidfVectorizer(stop_words='english', max_df=0.7)
tfidf_train = tfidf_vectorizer.fit_transform(X)
tfidf_test = tfidf_vectorizer.transform(Xt)

In [12]:
pp(count_vectorizer.get_feature_names()[0:10])
pp(count_vectorizer.get_feature_names()[-10:])


['00',
 '000',
 '0000',
 '00000031',
 '000035',
 '00006',
 '0001',
 '0001pt',
 '0002',
 '000billion']
['حلب', 'عربي', 'عن', 'لم', 'ما', 'محاولات', 'من', 'هذا', 'والمرضى', 'ยงade']


In [13]:
pp(tfidf_vectorizer.get_feature_names()[:10])
pp(tfidf_vectorizer.get_feature_names()[-10:])

['00',
 '000',
 '0000',
 '00000031',
 '000035',
 '00006',
 '0001',
 '0001pt',
 '0002',
 '000billion']
['حلب', 'عربي', 'عن', 'لم', 'ما', 'محاولات', 'من', 'هذا', 'والمرضى', 'ยงade']


In [20]:
#count_df = pd.DataFrame(count_train.A, columns=count_vectorizer.get_feature_names())
#tfidf_df = pd.DataFrame(count_train.A, columns=tfidf_vectorizer.get_feature_names())
#diff = set(count_df.columns) - set(tfidf_df.columns)
#pp(count_df.equals(tfidf_df))

In [38]:
clf = MultinomialNB()
clf.fit(tfidf_train, y)
pred = clf.predict(tfidf_test)
score = metrics.accuracy_score(yt, pred)
pp("score: " + str(score))
cm = metrics.confusion_matrix(yt, pred, labels=["FAKE", "REAL"])
plot_confusion_matrix(cm, classes=["FAKE", "REAL"], title= "tfidf")

'score: 0.8527091004734351'


FigureCanvasNbAgg()

Confusion matrix, without normalization
